In [1]:
!pip install -q git+https://github.com/huggingface/transformers.git
!pip install -q accelerate datasets peft bitsandbytes


[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: python -m pip install --upgrade pip


In [2]:
import torch
from datasets import load_dataset, Dataset
from transformers import AutoTokenizer, LlamaForCausalLM, BitsAndBytesConfig, HfArgumentParser, TrainingArguments, Trainer

from peft import prepare_model_for_kbit_training, LoraConfig, get_peft_model

In [22]:
bnb_config = BitsAndBytesConfig(
            load_in_4bit=True,
            bnb_4bit_quant_type="nf4",
            bnb_4bit_compute_dtype=torch.float16
        )
config = LoraConfig(
    r=8,
    lora_alpha=16,
    target_modules=["q_proj","k_proj","v_proj"],
    lora_dropout=0.1,
    bias="none",
    task_type="CAUSAL_LM"
)

model_name = "defog/llama-3-sqlcoder-8b"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = LlamaForCausalLM.from_pretrained(model_name, device_map = "cuda:0", torch_dtype=torch.float16, quantization_config = bnb_config)

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:601: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:601: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(


In [23]:
model = get_peft_model(model,config)
model.to("cuda")
model.print_trainable_parameters()

trainable params: 4,718,592 || all params: 8,034,979,840 || trainable%: 0.0587


In [12]:
tokenizer.pad_token = tokenizer.eos_token

import json
with open("syntheticDbData.json","r") as f:
    data = json.load(f)
untokenized_dataset = Dataset.from_list(data)

def preprocess_function(examples):
    inputs = tokenizer(examples["question"], padding="max_length", truncation=True, max_length=512)
    labels = tokenizer(examples["query"], padding="max_length", truncation=True, max_length=512)
    labels["input_ids"] = [-100 if token == tokenizer.pad_token_id else token for token in labels["input_ids"]]
    return {"input_ids": inputs["input_ids"], "attention_mask": inputs["attention_mask"], "labels": labels["input_ids"]}

ds = untokenized_dataset.map(preprocess_function, batched=True)
ds = ds.train_test_split(test_size=0.1)

Map:   0%|          | 0/121 [00:00<?, ? examples/s]

In [31]:
ds

DatasetDict({
    train: Dataset({
        features: ['question', 'query', 'input_ids', 'attention_mask', 'labels'],
        num_rows: 108
    })
    test: Dataset({
        features: ['question', 'query', 'input_ids', 'attention_mask', 'labels'],
        num_rows: 13
    })
})

In [7]:
prompt_template = lambda user_query: f"""
<|begin_of_text|><|start_header_id|>user<|end_header_id|>

Generate a SQL query to answer this question: `{user_query}`
if the question cannot be answered given the database schema, return "I do not know"

DDL statements:
CREATE DATABASE CarDealershipDB; USE CarDealershipDB; CREATE TABLE cars (serialNum INT PRIMARY KEY, make VARCHAR(50), model VARCHAR(50), mpg DECIMAL(5, 2), totalMiles INT, modelYear INT, color VARCHAR(20), engineType VARCHAR(50), registrationState VARCHAR(2), options TEXT); CREATE TABLE owners (ownerID INT PRIMARY KEY AUTO_INCREMENT, firstName VARCHAR(50), lastName VARCHAR(50), email VARCHAR(100), phoneNumber VARCHAR(15), address VARCHAR(255), city VARCHAR(100), state VARCHAR(2), zipCode VARCHAR(10), registrationDate DATE); CREATE TABLE dealerships (dealershipID INT PRIMARY KEY AUTO_INCREMENT, dealershipName VARCHAR(100), city VARCHAR(100), state VARCHAR(2), zipCode VARCHAR(10), phoneNumber VARCHAR(15), email VARCHAR(100), website VARCHAR(255), numEmployees INT, yearEstablished INT, avgMonthlySales DECIMAL(10, 2)); CREATE TABLE sales (saleID INT PRIMARY KEY AUTO_INCREMENT, serialNum INT, ownerID INT, dealershipID INT, sellPrice DECIMAL(10, 2), sellDate DATE, salesPersonID INT, financingType VARCHAR(50), paymentMethod VARCHAR(50), warrantyType VARCHAR(50), FOREIGN KEY (serialNum) REFERENCES cars(serialNum), FOREIGN KEY (ownerID) REFERENCES owners(ownerID), FOREIGN KEY (dealershipID) REFERENCES dealerships(dealershipID)); CREATE TABLE service_records (serviceID INT PRIMARY KEY AUTO_INCREMENT, serialNum INT, serviceDate DATE, serviceType VARCHAR(100), serviceCenter VARCHAR(100), serviceCost DECIMAL(10, 2), mileageAtService INT, serviceNotes TEXT, serviceManagerID INT, warrantyCovered BOOLEAN, FOREIGN KEY (serialNum) REFERENCES cars(serialNum));

The following SQL query best answers the question `{user_query}`:
```sql
"""

In [8]:
import torch

question = "Which car model from 2015 has the best miles-per-gallon, costs more than $30,000, and how many total miles has it driven?"

input = prompt_template(question)

inputs = tokenizer(input, return_tensors="pt", padding="max_length", truncation=True, max_length=512).to("cuda")

model.eval()

with torch.no_grad():
    generated_ids = model.generate(
        input_ids=inputs["input_ids"],
        attention_mask=inputs["attention_mask"],
        max_new_tokens=200,  # Allow for sufficient token generation
        repetition_penalty=2.0,
        early_stopping=True,
        eos_token_id=tokenizer.eos_token_id,  # Use greedy decoding for deterministic output
    )


generated_sql_query = tokenizer.decode(generated_ids[0], skip_special_tokens=True)
print(f"Generated SQL: {generated_sql_query}")

Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


Generated SQL: 
user

Generate a SQL query to answer this question: `Which car model from 2015 has the best miles-per-gallon, costs more than $30,000, and how many total miles has it driven?`
if the question cannot be answered given the database schema, return "I do not know"

DDL statements:
CREATE DATABASE CarDealershipDB; USE CarDealershipDB; CREATE TABLE cars (serialNum INT PRIMARY KEY, make VARCHAR(50), model VARCHAR(50), mpg DECIMAL(5, 2), totalMiles INT, modelYear INT, color VARCHAR(20), engineType VARCHAR(50), registrationState VARCHAR(2), options TEXT); CREATE TABLE owners (ownerID INT PRIMARY KEY AUTO_INCREMENT, firstName VARCHAR(50), lastName VARCHAR(50), email VARCHAR(100), phoneNumber VARCHAR(15), address VARCHAR(255), city VARCHAR(100), state VARCHAR(2), zipCode VARCHAR(10), registrationDate DATE); CREATE TABLE dealerships (dealershipID INT PRIMARY KEY AUTO_INCREMENT, dealershipName VARCHAR(100), city VARCHAR(100), state VARCHAR(2), zipCode VARCHAR(10), phoneNumber VARCHA

In [26]:
from typing import List, Dict, Any

class MyDataCollator:
    def __init__(self, tokenizer=tokenizer, max_length: int = 512):
        self.tokenizer = tokenizer
        self.max_length = max_length
        if self.tokenizer.pad_token is None:
            self.tokenizer.pad_token = self.tokenizer.eos_token

    def __call__(self, batch: List[Dict[str, Any]]) -> Dict[str, torch.Tensor]:
        questions = [prompt_template(item['question']) for item in batch]
        queries = [item['query'] for item in batch]
        # Tokenize the queries (labels) first
        labels = self.tokenizer(queries,padding="longest",truncation=True,max_length=self.max_length,return_tensors="pt")
        max_label_length = labels['input_ids'].size(1)  # Length of labels is longer than length of questions, so I had to pad 'backwards'.
        inputs = self.tokenizer(questions,padding="max_length",truncation=True,max_length=max_label_length,return_tensors="pt")
        

        labels["input_ids"][labels["input_ids"] == self.tokenizer.pad_token_id] = -100

        return {"input_ids": inputs["input_ids"],"attention_mask": inputs["attention_mask"],"labels": labels["input_ids"]}


In [38]:
from transformers import Trainer, TrainingArguments, EarlyStoppingCallback

# Define TrainingArguments
training_args = TrainingArguments(
    output_dir="./results",
    per_device_train_batch_size=2,  
    gradient_accumulation_steps=8, 
    evaluation_strategy="steps",    # Evaluate frequently to monitor overfitting
    eval_steps=10,                 
    num_train_epochs=50,            # Train for more epochs but monitor early stopping
    learning_rate=5e-5,             # Lower learning rate for more gradual updates
    weight_decay=0.01,             
    save_total_limit=2,         
    save_steps=10,                
    logging_steps=5,               
    load_best_model_at_end=True,   
    remove_unused_columns=False,     # Do NOT Remove columns not used by the model -> this process includes applying a prompt_template() function in the DataCollator that needs these 'unused' columns
    fp16=True,                      # Mixed precision to save memory
    warmup_steps=50,                
    logging_dir="./logs",         
)

# Early stopping callback
early_stopping = EarlyStoppingCallback(
    early_stopping_patience=3  # Stop if validation performance doesn't improve for 3 evals
)

# Initialize the Trainer with early stopping
trainer = Trainer(
    model=model,                   # Your model
    args=training_args,             # Training arguments
    train_dataset=ds['train'],    # Your training dataset
    eval_dataset=ds['train'],      # Your validation dataset
    tokenizer=tokenizer,            # Tokenizer
    data_collator = MyDataCollator(),
    callbacks=[early_stopping]      # Use early stopping to avoid overfitting
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1545: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
Detected kernel version 5.4.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [39]:
trainer.train()

/usr/local/lib/python3.10/dist-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


/usr/local/lib/python3.10/dist-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
/usr/local/lib/python3.10/dist-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
/usr/local/lib/python3.10/dist-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '
/usr/local/lib/python3.10/dist-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead u

TrainOutput(global_step=50, training_loss=7.076540489196777, metrics={'train_runtime': 1283.6677, 'train_samples_per_second': 4.207, 'train_steps_per_second': 0.039, 'total_flos': 9957786968064000.0, 'train_loss': 7.076540489196777, 'epoch': 28.571428571428573})

In [47]:
import torch

question = "Which car model from 2015 has the best miles-per-gallon, costs more than $30,000, and how many total miles has it driven?"
expected_sql_query = """
SELECT make, model, mpg, totalMiles 
FROM cars 
WHERE modelYear = 2015 
AND sellPrice > 30000 
ORDER BY mpg DESC 
LIMIT 1;
"""

inputs = tokenizer(prompt_template(question), return_tensors="pt", padding="max_length", truncation=True, max_length=512).to("cuda")

model.eval()

with torch.no_grad():
    generated_ids = model.generate(
        input_ids=inputs["input_ids"],
        attention_mask=inputs["attention_mask"],
        max_new_tokens=200,  # Allow for sufficient token generation
        repetition_penalty=2.0,
        early_stopping=True,
        eos_token_id=tokenizer.eos_token_id,  # Use greedy decoding for deterministic output
    )


generated_sql_query = tokenizer.decode(generated_ids[0], skip_special_tokens=True)
print(f"Generated SQL: {generated_sql_query}")

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:601: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:649: UserWarning: `num_beams` is set to 1. However, `early_stopping` is set to `True` -- this flag is only used in beam-based generation modes. You should set `num_beams>1` or unset `early_stopping`.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


Generated SQL: 
user

Generate a SQL query to answer this question: `Which car model from 2015 has the best miles-per-gallon, costs more than $30,000, and how many total miles has it driven?`
if the question cannot be answered given the database schema, return "I do not know"

DDL statements:
CREATE DATABASE CarDealershipDB; USE CarDealershipDB; CREATE TABLE cars (serialNum INT PRIMARY KEY, make VARCHAR(50), model VARCHAR(50), mpg DECIMAL(5, 2), totalMiles INT, modelYear INT, color VARCHAR(20), engineType VARCHAR(50), registrationState VARCHAR(2), options TEXT); CREATE TABLE owners (ownerID INT PRIMARY KEY AUTO_INCREMENT, firstName VARCHAR(50), lastName VARCHAR(50), email VARCHAR(100), phoneNumber VARCHAR(15), address VARCHAR(255), city VARCHAR(100), state VARCHAR(2), zipCode VARCHAR(10), registrationDate DATE); CREATE TABLE dealerships (dealershipID INT PRIMARY KEY AUTO_INCREMENT, dealershipName VARCHAR(100), city VARCHAR(100), state VARCHAR(2), zipCode VARCHAR(10), phoneNumber VARCHA

In [44]:
from huggingface_hub import login
login()

In [46]:
model.push_to_hub("QLoRA-text2sql-model")
# tokenizer.push_to_hub("./finetuned-sql-model")

adapter_model.safetensors:   0%|          | 0.00/18.9M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/kristiannordby/QLoRA-text2sql-model/commit/185f5a4d27fcd8da7bf93e0d917c71eac7876215', commit_message='Upload model', commit_description='', oid='185f5a4d27fcd8da7bf93e0d917c71eac7876215', pr_url=None, repo_url=RepoUrl('https://huggingface.co/kristiannordby/QLoRA-text2sql-model', endpoint='https://huggingface.co', repo_type='model', repo_id='kristiannordby/QLoRA-text2sql-model'), pr_revision=None, pr_num=None)